In [1]:
%load_ext autoreload
%autoreload 2

In [67]:
import sys
import dill
import numpy as np
import pandas as pd
import scipy.io as io
import datetime
import h5py
import matplotlib.pyplot as plt
import plotly.express as px

sys.path.append('../helper_functions')
sys.path.append('helper_functions')
sys.path.append('../objects')
sys.path.append('objects')

In [3]:
from FishGeneration import FishGeneration
from Fish_IceCreamCone import IceCreamConeFish
from Fish_Capsule import CapsuleFish

from assertion_tests import run_tests
run_tests()

'Success!'

In [4]:
dataset = dill.load(open("processed/data-2024_06_05-R_and_C_feature_space/dataset.pkl", "rb"))
leods = h5py.File("processed/data-2024_06_05-R_and_C_feature_space/leods.hdf5",'r')["localEODs"][:]
responses = h5py.File("processed/data-2024_06_05-R_and_C_feature_space/responses.hdf5",'r')["responses"][:]

In [5]:
leods.shape, responses.shape

((450000, 3, 1005), (450000, 3, 2))

In [6]:
list(dataset.keys())

['worms', 'fish', 'aquarium', 'electric_images']

In [55]:
eis = dataset["electric_images"]["pert"]
aquas = dataset["aquarium"]["dataframe"]
worms = dataset["worms"]["dataframe"]
main_df = eis.join(aquas[["conductivities"]].reset_index(names="aqua_id"), on="aqua_id", rsuffix="_R").join(
    worms[["resistances", "capacitances", "position_ys"]].reset_index(names="worm_id"), on="worm_id", rsuffix="_R"
)

In [88]:
feats = responses[main_df[(main_df["aqua_id"] == 1)].index][:,1]
dists = dataset["worms"]["position_ys"][main_df[(main_df["aqua_id"] == 1)]["position_ys"]]
plot_df = pd.DataFrame(np.vstack([feats.T, dists]).T, columns=["mz", "dlz", "distance"])

In [105]:
fig = px.scatter_3d(plot_df[plot_df["distance"]>0.02], x="mz", y="dlz", z="distance", color="distance", opacity=0.5)
fig.update_traces(marker_size = 1)
fig.update_layout(width=1000, height=1000)
fig.show()